In [ ]:
!pip install osmium

In [1]:
import osmium as osm
import pandas as pd
import folium
import copy

In [2]:
from osm_handler import OSMHandler

In [14]:
class OSMHandler(osm.SimpleHandler):
    def __init__(self):
        osm.SimpleHandler.__init__(self)
        self.nodes = []
        self.ways = []
        self.relations = []
        self.data = []

    def tag_inventory(self, elem, elem_type):
        for tag in elem.tags:
            self.data.append([elem_type, 
                              elem.id,
                              elem.version,
                              elem.visible,
                              pd.Timestamp(elem.timestamp),
                              elem.uid,
                              elem.user,
                              elem.changeset,
                              len(elem.tags)])

    def node(self, n):
        self.tag_inventory(n, "node")
        self.nodes.append(["node", n.id, n.location])

    def way(self, w):
        self.tag_inventory(w, "way")
        info = {}
        waypoints = []
        for tag in w.tags:
            info.update({(tag.k,tag.v)})
        for node in w.nodes:
            waypoints.append(node.ref)
        self.ways.append([w.id, waypoints,  info])
        #print(w)

    def relation(self, r):
        self.tag_inventory(r, "relation")
        if 'name' in r.tags:
            if 'NFTA' in r.tags['name']:
                info = {}
                waypoints = []
                for tag in r.tags:
                    info.update({(tag.k,tag.v)})
                for node in r.members:
                    waypoints.append(node.ref)
                    #waypoints.append(node)
                    #print('{},{},{}'.format(node.ref, node.role, node.type))
                self.relations.append([r.id, waypoints, info])
                print(r.tags['name'])
osmhandler = OSMHandler()
osmhandler.apply_file("unreasonably_large_map.osm")

NFTA 40A Buffalo-Niagara Falls via Grand Island
NFTA 23A Fillmore-Hertel (to Black Rock Riverside Transit Hub)
NFTA 15A Seneca
NFTA 23A Fillmore-Hertel (to Bailey & Abbott)
NFTA Metro Rail: Erie Canal Harbor → University
NFTA 2B Clinton (inbound)
NFTA 2B Clinton (outbound)
NFTA 2A Clinton (outbound)
NFTA 2A Clinton (inbound)
NFTA 1B William (outbound)
NFTA 1B William (inbound)
NFTA 11A Colvin (outbound)
NFTA 11A Colvin (inbound)
NFTA 4B Broadway (outbound)
NFTA 4B Broadway (inbound)
NFTA 4A Broadway (outbound)
NFTA 4A Broadway (inbound)
NFTA 20A Elmwood
NFTA 11D Colvin (outbound)
NFTA 11D Colvin (inbound)
NFTA 1A William (outbound)
NFTA 1A William (inbound)
NFTA 14A Abbott
NFTA 14B Abbott
NFTA 14C Abbott
NFTA 13A Kensington
NFTA 12A Utica
NFTA 8A Main
NFTA 7A Baynes-Richmond
NFTA 6A Sycamore
NFTA 5A Niagara-Kenmore
NFTA 3A Grant
NFTA 22A Porter-Best
NFTA 19A Bailey
NFTA 18A Jefferson
NFTA 16H South Park
NFTA 16A South Park
NFTA 16B South Park
NFTA 32A Amherst
NFTA 29A Wohlers
NFTA 26A 

In [15]:
latitudes = []
longitudes = []
node_table = {}
for node in osmhandler.nodes:
    latitudes.append(node[2].lat)
    longitudes.append(node[2].lon)
    node_table.update({node[1]:[node[2].lat,node[2].lon]})
print(len(latitudes))

3762720


In [16]:
ways = []
for way in osmhandler.ways:
    ways.append(way)
#print(len(ways))

In [17]:
relations = []
for relation in osmhandler.relations:
    relations.append(relation)
#print(len(relations))

In [18]:
way_table = {}
for way in ways:
    way_table.update({way[0]:way[1]})
#print(way_table)

In [19]:
used_nodes = set()
used_ways = set()

for relation in relations:
    for index in relation[1]:
        if index in way_table:
            used_ways.add(index)
            #print(index)
            for waypoint in way_table[index]:
                used_nodes.add(waypoint)
                #print('({},{})'.format(node_table[waypoint][0],node_table[waypoint][1]))
        elif index in node_table:
            used_nodes.add(waypoint)
            #print('({},{})'.format(node_table[index][0], node_table[index][1]))

print(len(used_nodes))
print(len(used_ways))

19889
2783


In [20]:
m = folium.Map(location=[42.89, -78.74], tiles="OpenStreetMap", zoom_start=10)

for relation in relations[0:5]:
    print(relation[2]['name'])
    for index in relation[1]:
        points = []
        if index in way_table:
            for waypoint in way_table[index]:
                folium.Marker([node_table[waypoint][0], node_table[waypoint][1]]).add_to(m)
                points.append((node_table[waypoint][0], node_table[waypoint][1]))
        elif index in node_table:
            folium.Marker([node_table[index][0], node_table[index][1]]).add_to(m)
            points.append((node_table[index][0], node_table[index][1]))
        if(len(points) != 0):
            #print('points: {}'.format(points))
            folium.PolyLine(points).add_to(m)

NFTA 40A Buffalo-Niagara Falls via Grand Island
NFTA 23A Fillmore-Hertel (to Black Rock Riverside Transit Hub)
NFTA 15A Seneca
NFTA 23A Fillmore-Hertel (to Bailey & Abbott)
NFTA Metro Rail: Erie Canal Harbor → University


In [21]:
#m

In [22]:
final_node_table = {}
final_way_table = {}

for key,value in node_table.items():
    if key in used_nodes:
        final_node_table.update({key:value})
        
for key,value in way_table.items():
    if key in used_ways:
        final_way_table.update({key:value})
print(len(final_node_table))
print(len(final_way_table))

19889
2783


In [23]:
import random

m = folium.Map(location=[42.89, -78.74], tiles="OpenStreetMap", zoom_start=10)

for relation in relations:
    line_color = '#{}'.format(hex(random.randint(0,16777215))[2:])
    print(relation[2]['name'])
    for index in relation[1]:
        points = []
        if index in final_way_table:
            for waypoint in final_way_table[index]:
                #folium.Marker([final_node_table[waypoint][0], final_node_table[waypoint][1]]).add_to(m)
                points.append((final_node_table[waypoint][0], final_node_table[waypoint][1]))
        elif index in final_node_table:
            #folium.Marker([final_node_table[index][0], final_node_table[index][1]]).add_to(m)
            points.append((final_node_table[index][0], final_node_table[index][1]))
        if(len(points) != 0):
            folium.PolyLine(points, color=line_color).add_to(m)
m

NFTA 40A Buffalo-Niagara Falls via Grand Island
NFTA 23A Fillmore-Hertel (to Black Rock Riverside Transit Hub)
NFTA 15A Seneca
NFTA 23A Fillmore-Hertel (to Bailey & Abbott)
NFTA Metro Rail: Erie Canal Harbor → University
NFTA 2B Clinton (inbound)
NFTA 2B Clinton (outbound)
NFTA 2A Clinton (outbound)
NFTA 2A Clinton (inbound)
NFTA 1B William (outbound)
NFTA 1B William (inbound)
NFTA 11A Colvin (outbound)
NFTA 11A Colvin (inbound)
NFTA 4B Broadway (outbound)
NFTA 4B Broadway (inbound)
NFTA 4A Broadway (outbound)
NFTA 4A Broadway (inbound)
NFTA 20A Elmwood
NFTA 11D Colvin (outbound)
NFTA 11D Colvin (inbound)
NFTA 1A William (outbound)
NFTA 1A William (inbound)
NFTA 14A Abbott
NFTA 14B Abbott
NFTA 14C Abbott
NFTA 13A Kensington
NFTA 12A Utica
NFTA 8A Main
NFTA 7A Baynes-Richmond
NFTA 6A Sycamore
NFTA 5A Niagara-Kenmore
NFTA 3A Grant
NFTA 22A Porter-Best
NFTA 19A Bailey
NFTA 18A Jefferson
NFTA 16H South Park
NFTA 16A South Park
NFTA 16B South Park
NFTA 32A Amherst
NFTA 29A Wohlers
NFTA 26A 

In [24]:
import pickle 
with open('graph/final_node_table', 'wb') as f: 
    pickle.dump(final_node_table, f) 
with open('graph/final_way_table', 'wb') as f:
    pickle.dump(final_way_table, f)
with open('graph/relations', 'wb') as f:
    pickle.dump(relations, f)

In [132]:
with open('graph/final_node_table', 'rb') as f: 
    final_node_table = pickle.load(f)
with open('graph/final_way_table', 'rb') as f:
    final_way_table = pickle.load(f)
with open('graph/relations', 'rb') as f:
    relations = pickle.load(f)